In [24]:
import pandas as pd
import numpy as np
import random 
import plotly.graph_objects as go
from scipy.stats import norm

In [25]:
def bm_simulations(n_paths, granularity, max_time):
    n_steps = granularity * max_time
    
    paths = []
    for i in range(n_paths):
        xs = random.choices([-1, 1], weights = [0.5, 0.5], k = n_steps)
        xs = [0] + xs
        path = np.cumsum(xs)/np.sqrt(granularity)
        paths.append(path)
        
    return paths

$$V_t= \mu+\frac{\sigma}{\sqrt{2\theta}}e^{-\theta t} W_{e^{2\theta t}}$$
 
Using the method, proved in the article.

In [26]:
sigma=1
theta=1
OU_0=0

N=1
n=100
t=2

paths=[]

for _ in range(N):

    t_=np.linspace(0,t, n*t+1)

    W_phi=[OU_0]

    for i in range(1,len(t_)):
        incr=norm.rvs(loc=0, scale=np.power(np.exp(2*theta*t_[i])-np.exp(2*theta*t_[i-1]),2))
        W_phi.append(incr)
        
    
    W_phi=np.array(W_phi)
    W_phi=np.cumsum(W_phi)
    mult=sigma/np.sqrt(2*theta)*np.exp(-1*theta*t_)


    path=W_phi*mult
    paths.append(path)



In [106]:
def Ornstein_Ukhlenbeck(sigma, theta, mu, N, n, t):
    
    t_=np.linspace(0,t, n*t+1)
    mult=sigma/np.sqrt(2*theta)*np.exp(-1*theta*t_)
    
    paths=[]
    for _ in range(N):
        OU_0=norm.rvs(loc=0, scale=sigma/np.sqrt(2*theta))
        OU_0_=OU_0/mult[0]
        W_phi=[OU_0_]
        for i in range(1,len(t_)):
            incr=norm.rvs(loc=0, scale=np.sqrt(np.exp(2*theta*t_[i])-np.exp(2*theta*t_[i-1])))
            W_phi.append(incr)
        
        W_phi=np.array(W_phi)
        W_phi=np.cumsum(W_phi)
        path=W_phi*mult+mu
        paths.append(path)
    return t_, paths

In [ ]:
# def Ornstein_Ukhlenbeck(sigma, theta, OU_0, N, n, t):
    
#     t_=np.linspace(0,t, n*t+1)
#     mult=sigma/np.sqrt(2*theta)*np.exp(-1*theta*t_)
#     OU_0_=OU_0/mult[0]
#     paths=[]
#     for _ in range(N):
#         W_phi=[OU_0_]
#         for i in range(1,len(t_)):
#             incr=norm.rvs(loc=0, scale=np.sqrt(np.exp(2*theta*t_[i])-np.exp(2*theta*t_[i-1])))
#             W_phi.append(incr)
        
#         W_phi=np.array(W_phi)
#         W_phi=np.cumsum(W_phi)
#         path=W_phi*mult
#         paths.append(path)
#     return t_, paths

In [107]:
sigma=0.1
theta=3
mu=10
N=2
n=10
t=2
t,path=Ornstein_Ukhlenbeck(sigma, theta, mu, N, n, t)

path

[array([ 9.97588328, 10.01357073, 10.03721464, 10.01904482, 10.02722083,
         9.98955021, 10.01454424, 10.03114044, 10.05988589, 10.01830343,
        10.0483593 , 10.05863008, 10.02649056, 10.01967555, 10.04896685,
        10.01000049,  9.99839466,  9.99755553, 10.00830085, 10.02098703,
        10.00129347]),
 array([ 9.94697248,  9.94375619,  9.93177688,  9.96733033,  9.97475799,
         9.93274138,  9.91771477,  9.97259635,  9.96376657,  9.9423433 ,
        10.00290789,  9.95840355,  9.92793873,  9.96016312,  9.98026546,
         9.99408015, 10.01532657, 10.05419068, 10.06163245, 10.05882989,
        10.01149507])]

In [70]:
# alpha=1
# beta=1
# N=3
# n=10
# t=1
# t_=np.linspace(0,t, n*t+1)
# exps=np.exp(-beta*t_)


# t_modif=alpha*np.exp(2*beta*t_)

# max_t=max(t_modif)
# t_for_w=np.linspace(0, max_t, int(max_t*n))
# w_t=bm_simulations(1, n, int(max_t))


In [115]:
sigma=0.2
theta=1
mu=20
N=200
n=100
t=20



t_, paths_=Ornstein_Ukhlenbeck(sigma, theta, mu, N, n, t)
plot=go.Figure()
for i in paths_:
    graph=go.Scatter(x=t_, y=i)
    plot.add_trace(graph)
plot.show()

# Unit tests (Process validation)

In [116]:
sigma=0.6
theta=3
mu=0
N=30000
n=100
t=2

t_, paths=Ornstein_Ukhlenbeck(sigma, theta, mu, N, n, t)

X1_sample=[path[int(t*n/2)] for path in paths]
X1_bar=np.mean(X1_sample)
X1_var=np.var(X1_sample)


X2_sample=([path[-1] for path in paths])
X2_bar=np.mean(X2_sample)
X2_var=np.var(X2_sample)


X1_X2_cov=np.cov(X1_sample,X2_sample)


print(f'difference between E(X_10) practical and theoretical:{abs(X1_bar-mu)}')
print(f'difference between E(X_20) practical and theoretical:{abs(X2_bar-mu)}')
print(f'difference between Var(X_10) practical and theoretical:{abs(X1_var-(sigma**2/(2*theta))*(1-np.exp(-2*theta*t/2)))}')
print(f'difference between Var(X_20) practical and theoretical:{abs(X2_var-(sigma**2/(2*theta))*(1-np.exp(-2*theta*t)))}')

print(f'difference between Cov(X_10,X_20) practical and theoretical:{abs(X1_X2_cov[0,1]-sigma**2/(2*theta)*(np.exp(-theta*t/2)-np.exp(-theta*1.5*t)))}')


print(X1_X2_cov)

difference between E(X_10) practical and theoretical:0.00039037072180002737
difference between E(X_20) practical and theoretical:0.0010897290847172553
difference between Var(X_10) practical and theoretical:0.0016347163660319491
difference between Var(X_20) practical and theoretical:0.000682023719858163
difference between Cov(X_10,X_20) practical and theoretical:0.00039673779299352055
[[0.06148804 0.00337656]
 [0.00337656 0.06068368]]


In [31]:
# alpha=1
# beta=1
# N=3
# n=100
# t=3
# X0=1
# t_=np.linspace(0,t, n*t+1)

# exps=np.exp(-beta*t_)
# t_modif=alpha*np.exp(2*beta*t_)


# W_t=bm_simulations(1, n, t)
# t_new=np.sqrt(t_modif[1:]/t_[1:])
# w_t_adj=t_new*W_t[0][1:] *exps[1:]
# w_t_adj=np.insert(w_t_adj, 0, X0)
# plot=go.Figure()
# graph=go.Scatter(x=t_, y=w_t_adj, mode='lines')
# plot.add_trace(graph)


In [32]:
# alpha=1
# beta=1
# N=3
# granularity=100
# max_time=3
# X0=1
# t_=np.linspace(0,max_time, granularity*max_time+1)
# n_steps = granularity * max_time


# mults=[]
# incr=norm.rvs(loc=0, scale=np.sqrt(granularity), size=n_steps)
# for i in range(1, len(t_)):
#     mult_i=np.sqrt(alpha)*(np.exp(beta*t_[i])-np.exp(beta*t_[i-1]))
#     mults.append(mult_i)
# mults=np.array(mults)
# X_t=mults*incr
# X_t=np.insert(X_t, 0, X0)
# path=np.cumsum(X_t)

# plot=go.Figure()
# graph=go.Scatter(x=t_, y=path, mode='lines')
# plot.add_trace(graph)

## Life hack)

In [33]:
a=[1, 2, 3]
b=[6,7,8]
dict_=dict(zip(a,b))
dict_

{1: 6, 2: 7, 3: 8}

In [34]:

# plot=go.Figure()
# graph=go.Scatter(x=t_, y=paths, mode='lines')
# plot.add_trace(graph)